In [1]:
import shutil
import os
import platform
from pathlib import Path
from cadet import Cadet

import os

from IPython.core.display import display, HTML, clear_output
#display(HTML("<style>.container { width:100% !important; }</style>"))

from IPython.display import Image

# python numeric library
import numpy as np

# scientific library for python
import scipy

# addict is a library that makes it easier to create nested dictionaries
from addict import Dict

# json is a standard text based format and it used in CADETMatch for the configuration file
import json

# python plotting library
import matplotlib.pyplot as plt
%config InlineBackend.figure_format='svg'
%matplotlib inline

# jupyter widget support
from ipywidgets import interact, interactive
import ipywidgets as widgets

# Temporary files for simulation objects
import tempfile
tempfile.tempdir = os.path.join(Path.home())

import subprocess
import pandas as pd

In [2]:
# # Convert lab result to accepted CSV file
# lab_result = pd.read_excel('./u=2.7.xlsx')
# c_ini = 4.762

# time_min = lab_result['min']
# c = lab_result['c']

# # Extract targeted time index
# index_list = np.concatenate(([0], np.arange(29, len(time_min)+1, 30)))

# time_min_select = np.array(time_min[index_list])
# c_select = np.array(c[index_list])

# # Replace index 0 with 0 ICs
# time_min_select[0] = 0
# c_select[0] = 0
# c_select = c_select.clip(min=0)
# # Convert mins to seconds
# time_sec = time_min_select * 60

# # denormalize c
# c_sec = c_select*c_ini

# # Create csv file for Cadet Match
# result_df = pd.DataFrame()
# result_df['Time'] = time_sec
# result_df['c'] = c_sec

# result_df.to_csv('./u=2.7.csv', index=False, header=False)

In [3]:
def get_cadet_template(n_units=3, split_components_data=False):
    cadet_template = Cadet()
    
    cadet_template.root.input.model.nunits = n_units
    
    # Store solution
    cadet_template.root.input['return'].split_components_data = split_components_data
    cadet_template.root.input['return'].split_ports_data = 0
    cadet_template.root.input['return'].unit_000.write_solution_inlet = 1
    cadet_template.root.input['return'].unit_000.write_solution_outlet = 1
    cadet_template.root.input['return'].unit_000.write_solution_bulk = 1
    cadet_template.root.input['return'].unit_000.write_solution_particle = 1
    cadet_template.root.input['return'].unit_000.write_solution_solid = 1
    cadet_template.root.input['return'].unit_000.write_solution_flux = 1
    cadet_template.root.input['return'].unit_000.write_solution_volume = 1
    cadet_template.root.input['return'].unit_000.write_coordinates = 1
    cadet_template.root.input['return'].unit_000.write_sens_outlet = 1
    
    for unit in range(n_units):
        cadet_template.root.input['return']['unit_{0:03d}'.format(unit)] = cadet_template.root.input['return'].unit_000
        
    # Tolerances for the time integrator
    cadet_template.root.input.solver.time_integrator.abstol = 1e-6
    cadet_template.root.input.solver.time_integrator.algtol = 1e-10
    cadet_template.root.input.solver.time_integrator.reltol = 1e-6
    cadet_template.root.input.solver.time_integrator.init_step_size = 1e-6
    cadet_template.root.input.solver.time_integrator.max_steps = 1000000
    
    # Solver settings
    cadet_template.root.input.model.solver.gs_type = 1
    cadet_template.root.input.model.solver.max_krylov = 0
    cadet_template.root.input.model.solver.max_restarts = 10
    cadet_template.root.input.model.solver.schur_safety = 1e-8

    # Run the simulation on single thread
    cadet_template.root.input.solver.nthreads = 1
    
    return cadet_template

def set_discretization(model, n_bound=None, n_col=20, n_par_types=1):
    columns = {'GENERAL_RATE_MODEL', 'LUMPED_RATE_MODEL_WITH_PORES', 'LUMPED_RATE_MODEL_WITHOUT_PORES'}
    
    
    for unit_name, unit in model.root.input.model.items():
        if 'unit_' in unit_name and unit.unit_type in columns:
            unit.discretization.ncol = n_col
            unit.discretization.npar = 5
            unit.discretization.npartype = n_par_types
            
            if n_bound is None:
                n_bound = unit.ncomp*[0]
            unit.discretization.nbound = n_bound
            
            unit.discretization.par_disc_type = 'EQUIDISTANT_PAR'
            unit.discretization.use_analytic_jacobian = 1
            unit.discretization.reconstruction = 'WENO'
            unit.discretization.gs_type = 1
            unit.discretization.max_krylov = 0
            unit.discretization.max_restarts = 10
            unit.discretization.schur_safety = 1.0e-8

            unit.discretization.weno.boundary_model = 0
            unit.discretization.weno.weno_eps = 1e-10
            unit.discretization.weno.weno_order = 3
            
def run_simulation(cadet, file_name=None):
    if file_name is None:
        f = next(tempfile._get_candidate_names())
        cadet.filename = os.path.join(tempfile.tempdir, f + '.h5')
    else:
        cadet.filename = file_name
    # save the simulation
    cadet.save()

    # run the simulation and load results
    data = cadet.run()
    cadet.load()
    
    # Remove files 
    if file_name is None:
        os.remove(os.path.join(tempfile.tempdir, f + '.h5'))

    # Raise error if simulation fails
    if data.returncode == 0:
        print("Simulation completed successfully")
    else:
        print(data)
        raise Exception("Simulation failed")

In [4]:
def create_langmuir_model(L, u, e, Da, ka, kd, qmax, c0, tmax, col_step, time_step):

    langmuir_model = get_cadet_template(n_units=3)

    # INLET
    langmuir_model.root.input.model.unit_000.unit_type = 'INLET'
    langmuir_model.root.input.model.unit_000.ncomp = 1
    langmuir_model.root.input.model.unit_000.inlet_type = 'PIECEWISE_CUBIC_POLY'

    # Column
    langmuir_model.root.input.model.unit_001.unit_type = 'LUMPED_RATE_MODEL_WITHOUT_PORES'
    langmuir_model.root.input.model.unit_001.ncomp = 1

    langmuir_model.root.input.model.unit_001.col_length = L
    langmuir_model.root.input.model.unit_001.velocity = u / e
    langmuir_model.root.input.model.unit_001.total_porosity = e
    langmuir_model.root.input.model.unit_001.col_dispersion = Da
    
    langmuir_model.root.input.model.unit_001.adsorption_model = 'MULTI_COMPONENT_LANGMUIR'

    langmuir_model.root.input.model.unit_001.adsorption.is_kinetic = True
    langmuir_model.root.input.model.unit_001.adsorption.mcl_ka = [ka,]
    langmuir_model.root.input.model.unit_001.adsorption.mcl_kd = [kd,]
    langmuir_model.root.input.model.unit_001.adsorption.mcl_qmax = [qmax,]

    langmuir_model.root.input.model.unit_001.init_c = [0.0,]
    langmuir_model.root.input.model.unit_001.init_q = [0.0,]

    ## Outlet
    langmuir_model.root.input.model.unit_002.ncomp = 1
    langmuir_model.root.input.model.unit_002.unit_type = 'OUTLET'
    
    set_discretization(langmuir_model, n_bound=[1,], n_col=col_step)

    # Sections and connections
    langmuir_model.root.input.solver.sections.nsec = 1
    langmuir_model.root.input.solver.sections.section_times = [0.0, tmax]
    langmuir_model.root.input.solver.sections.section_continuity = [0,]
    
    ## Inlet Profile
    langmuir_model.root.input.model.unit_000.sec_000.const_coeff = [c0,]
    
    Q = langmuir_model.root.input.model.unit_001.velocity
    
    ## Switches
    langmuir_model.root.input.model.connections.nswitches = 1
    langmuir_model.root.input.model.connections.switch_000.section = 0
    langmuir_model.root.input.model.connections.switch_000.connections = [
        0, 1, -1, -1, Q,
        1, 2, -1, -1, Q
    ]

    # set the times that the simulator writes out data for
    langmuir_model.root.input.solver.user_solution_times = np.linspace(0, tmax, time_step) 

    return langmuir_model

In [5]:
from addict import Dict

base_dir = Path('./').absolute()

match_config = Dict()
match_config.CADETPath = Cadet.cadet_path
match_config.baseDir = base_dir.as_posix()
match_config.resultsDir = 'results'

In [6]:
# Get tmax and time_step
result_df = pd.read_csv('./u=2.7.csv')
result_df

0.0     0.0.1
0        6.0  0.000000
1       12.0  0.000000
2       18.0  0.000000
3       24.0  0.000000
4       30.0  0.000000
...      ...       ...
1145  6876.0  4.642390
1146  6882.0  4.642946
1147  6888.0  4.643960
1148  6894.0  4.644739
1149  6900.0  4.645557

[1150 rows x 2 columns]

In [7]:
# Known parameters
L = 0.18
u = 2.7 / 3600
c0 = 4.762

# Unknown parameters --- Initial guess
e = 0.5
Da = 2e-5
ka = 1e-3
kd = 1e-3
qmax = 100

In [8]:
# get time_step
time_step = len(result_df['0.0'])
tmax = np.array(result_df['0.0'])[-1]
col_step = 20

print(col_step)
print(time_step)
print(tmax)

20
1150
6900.0


In [9]:
Cadet.cadet_path = 'C:/Users/yuan_yunhao/Miniconda3/envs/tf2/bin/cadet-cli.exe'

from addict import Dict

base_dir = Path('./').absolute()

match_config = Dict()
match_config.CADETPath = Cadet.cadet_path
match_config.baseDir = base_dir.as_posix()
match_config.resultsDir = 'results'

In [10]:
langumir_model = create_langmuir_model(L, u, e, Da, ka, kd, qmax, c0, tmax, col_step, time_step)
run_simulation(langumir_model, 'langmuir_reference.h5')

Simulation completed successfully


In [11]:
# e
parameter1 = Dict()
parameter1.location = '/input/model/unit_001/COL_POROSITY'
parameter1.min = 0.5
parameter1.max = 0.9
parameter1.component = -1
parameter1.bound = -1
parameter1.transform = 'null'

# Da
parameter2 = Dict()
parameter2.location = '/input/model/unit_001/COL_DISPERSION'
parameter2.min = 1e-9
parameter2.max = 1e-2
parameter2.component = -1
parameter2.bound = -1
parameter2.transform = 'auto'

# ka
parameter3 = Dict()
parameter3.transform = 'auto'
parameter3.component = 0
parameter3.bound = 0
parameter3.location = '/input/model/unit_001/adsorption/MCL_KA'
parameter3.min = 1e-5
parameter3.max = 1e5

# kd
parameter4 = Dict()
parameter4.transform = 'auto'
parameter4.component = 0
parameter4.bound = 0
parameter4.location = '/input/model/unit_001/adsorption/MCL_KD'
parameter4.min = 1e-5
parameter4.max = 1e5

# qmax
parameter5 = Dict()
parameter5.transform = 'auto'
parameter5.component = 0
parameter5.bound = 0
parameter5.location = '/input/model/unit_001/adsorption/MCL_QMAX'
parameter5.min = 0.5
parameter5.max = 200


match_config.parameters = [parameter1, parameter2, parameter3, parameter4, parameter5]

In [12]:
experiment1 = Dict()
experiment1.csv = './u=2.7.csv'
experiment1.output_path = '/output/solution/unit_002/SOLUTION_OUTLET_COMP_000'
experiment1.HDF5 = 'langmuir_reference.h5'
experiment1.name = 'main'

feature1 = Dict()
feature1.name = 'Pulse'
feature1.type = 'SSE'

experiment1.features = [feature1,]

match_config.experiments = [experiment1,]

match_config.searchMethod = 'NSGA3'
match_config.population = 12
match_config.stallGenerations = 10
match_config.finalGradRefinement = True
match_config.gradVector = True

In [13]:
from CADETMatch.jupyter import Match

match_file = base_dir / 'langmuir.json'

with open(match_file, 'w') as json_file:
    json.dump(match_config.to_dict(), json_file, indent='\t')

match = Match(match_file)
match.start_sim()

C:\Users\yuan_yunhao\Miniconda3\envs\tf2\lib\importlib\_bootstrap.py:219: RuntimeWarning: numpy.ndarray size changed, may indicate binary incompatibility. Expected 16 from C header, got 88 from PyObject
  return f(*args, **kwds)


2023-04-10 16:07:48,915 match.py print_version 122 CADETMatch starting up version: 0.8.16

2023-04-10 16:07:48,915 match.py print_version 154 attrs version: 22.1.0 tested with 21.2.0

2023-04-10 16:07:48,915 match.py print_version 154 joblib version: 1.2.0 tested with 1.0.1

2023-04-10 16:07:48,915 match.py print_version 154 addict version: 2.4.0 tested with 2.4.0

2023-04-10 16:07:48,915 match.py print_version 154 corner version: 2.2.1 tested with 2.2.1

2023-04-10 16:07:48,915 match.py print_version 154 emcee version: 3.1.4 tested with 3.0.2

2023-04-10 16:07:48,915 match.py print_version 154 SALib version: 1.4.5 tested with 1.3.11

2023-04-10 16:07:48,930 match.py print_version 154 psutil version: 5.9.4 tested with 5.8.0

2023-04-10 16:07:48,930 match.py print_version 154 numpy version: 1.21.5 tested with 1.21.1

2023-04-10 16:07:48,930 match.py print_version 154 openpyxl version: 3.1.2 tested with 3.0.7

2023-04-10 16:07:48,930 match.py print_version 154 scipy version: 1.7.3 tested